Lambda School Data Science

*Unit 2, Sprint 3, Module 2*

---


# Wrangle ML datasets

- [ ] Continue to clean and explore your data. 
- [ ] For the evaluation metric you chose, what score would you get just by guessing?
- [ ] Can you make a fast, first model that beats guessing?

**We recommend that you use your portfolio project dataset for all assignments this sprint.**

**But if you aren't ready yet, or you want more practice, then use the New York City property sales dataset for today's assignment.** Follow the instructions below, to just keep a subset for the Tribeca neighborhood, and remove outliers or dirty data. [Here's a video walkthrough](https://youtu.be/pPWFw8UtBVg?t=584) you can refer to if you get stuck or want hints!

- Data Source: [NYC OpenData: NYC Citywide Rolling Calendar Sales](https://data.cityofnewyork.us/dataset/NYC-Citywide-Rolling-Calendar-Sales/usep-8jbt)
- Glossary: [NYC Department of Finance: Rolling Sales Data](https://www1.nyc.gov/site/finance/taxes/property-rolling-sales-data.page)

In [1]:
%%capture
import sys

# If you're on Colab:
if 'google.colab' in sys.modules:
    DATA_PATH = 'https://raw.githubusercontent.com/LambdaSchool/DS-Unit-2-Applied-Modeling/master/data/'
    !pip install category_encoders==2.*
    !pip install pandas-profiling==2.*

# If you're working locally:
else:
    DATA_PATH = '../data/'

In [2]:
# Read New York City property sales data
import pandas as pd
df = pd.read_csv(DATA_PATH+'condos/NYC_Citywide_Rolling_Calendar_Sales.csv')

Your code starts here:

In [4]:
# Change column names: replace spaces with underscores
df.columns = df.columns.str.replace(' ', '_')

In [10]:
# Get Pandas Profiling Report
from pandas_profiling import ProfileReport
ProfileReport(df)

In [16]:
# Keep just the subset of data for the Tribeca neighborhood
# Check how many rows you have now. (Should go down from > 20k rows to 146)
tribeca = df[df['NEIGHBORHOOD']=='TRIBECA']
tribeca.shape

(146, 21)

In [17]:
tribeca.columns

Index(['BOROUGH', 'NEIGHBORHOOD', 'BUILDING_CLASS_CATEGORY',
       'TAX_CLASS_AT_PRESENT', 'BLOCK', 'LOT', 'EASE-MENT',
       'BUILDING_CLASS_AT_PRESENT', 'ADDRESS', 'APARTMENT_NUMBER', 'ZIP_CODE',
       'RESIDENTIAL_UNITS', 'COMMERCIAL_UNITS', 'TOTAL_UNITS',
       'LAND_SQUARE_FEET', 'GROSS_SQUARE_FEET', 'YEAR_BUILT',
       'TAX_CLASS_AT_TIME_OF_SALE', 'BUILDING_CLASS_AT_TIME_OF_SALE',
       'SALE_PRICE', 'SALE_DATE'],
      dtype='object')

In [21]:
# Q. What's the date range of these property sales in Tribeca?
earliest_date = tribeca['SALE_DATE'].min()
latest_date = tribeca['SALE_DATE'].max()
print(earliest_date,'-', latest_date)

01/03/2019 - 04/30/2019


In [44]:
# The Pandas Profiling Report showed that SALE_PRICE was read as strings
# Convert it to integers
tribeca['SALE_PRICE'] = tribeca['SALE_PRICE'].str.lstrip('-')
tribeca.head()

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


BOROUGH NEIGHBORHOOD  ... SALE_PRICE   SALE_DATE
220         1      TRIBECA  ...    2800000  01/03/2019
763         1      TRIBECA  ...    2650000  01/07/2019
996         1      TRIBECA  ...          0  01/08/2019
1276        1      TRIBECA  ...    1005000  01/09/2019
1542        1      TRIBECA  ...   12950000  01/10/2019

[5 rows x 21 columns]

In [45]:
tribeca['SALE_PRICE'] = tribeca['SALE_PRICE'].astype(int)
tribeca.dtypes

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


BOROUGH                             int64
NEIGHBORHOOD                       object
BUILDING_CLASS_CATEGORY            object
TAX_CLASS_AT_PRESENT               object
BLOCK                               int64
LOT                                 int64
EASE-MENT                         float64
BUILDING_CLASS_AT_PRESENT          object
ADDRESS                            object
APARTMENT_NUMBER                   object
ZIP_CODE                          float64
RESIDENTIAL_UNITS                 float64
COMMERCIAL_UNITS                  float64
TOTAL_UNITS                       float64
LAND_SQUARE_FEET                   object
GROSS_SQUARE_FEET                 float64
YEAR_BUILT                        float64
TAX_CLASS_AT_TIME_OF_SALE           int64
BUILDING_CLASS_AT_TIME_OF_SALE     object
SALE_PRICE                          int64
SALE_DATE                          object
dtype: object

In [46]:
# Q. What is the maximum SALE_PRICE in this dataset?
tribeca['SALE_PRICE'].max()

260000000

In [48]:
# Look at the row with the max SALE_PRICE
tribeca[tribeca['SALE_PRICE']==tribeca['SALE_PRICE'].max()]

BOROUGH NEIGHBORHOOD  ... SALE_PRICE   SALE_DATE
6499        1      TRIBECA  ...  260000000  02/01/2019

[1 rows x 21 columns]

In [54]:
# Get value counts of TOTAL_UNITS
# Q. How many property sales were for multiple units?
tribeca['TOTAL_UNITS'].value_counts()

1.0      131
0.0       11
5.0        1
286.0      1
8.0        1
3.0        1
Name: TOTAL_UNITS, dtype: int64

In [55]:
# Keep only the single units
tribeca_single = tribeca[tribeca['TOTAL_UNITS']==1]
tribeca_single['TOTAL_UNITS'].value_counts()

1.0    131
Name: TOTAL_UNITS, dtype: int64

In [57]:
# Q. Now what is the max sales price? How many square feet does it have?
print(tribeca_single['SALE_PRICE'].max())
tribeca_single[tribeca_single['SALE_PRICE']==tribeca_single['SALE_PRICE'].max()]
# Square footage = 8,346

39285000


BOROUGH NEIGHBORHOOD  ... SALE_PRICE   SALE_DATE
9236        1      TRIBECA  ...   39285000  02/15/2019

[1 rows x 21 columns]

In [65]:
# Q. How often did $0 sales occur in this subset of the data?

# There's a glossary here: 
# https://www1.nyc.gov/site/finance/taxes/property-rolling-sales-data.page

# It says:
# A $0 sale indicates that there was a transfer of ownership without a 
# cash consideration. There can be a number of reasons for a $0 sale including 
# transfers of ownership from parents to children. 

tribeca_single['SALE_PRICE'].value_counts()

0           15
36681561    15
2700000      2
4800000      2
4100000      2
            ..
1380000      1
7200000      1
3920263      1
1658000      1
9316988      1
Name: SALE_PRICE, Length: 98, dtype: int64

In [67]:
# Look at property sales for > 5,000 square feet
# Q. What is the highest square footage you see?
tribeca_single[tribeca_single['GROSS_SQUARE_FEET']>5000]
# Hightest square footage = 39,567

BOROUGH NEIGHBORHOOD  ... SALE_PRICE   SALE_DATE
9236         1      TRIBECA  ...   39285000  02/15/2019
10487        1      TRIBECA  ...    9857100  02/22/2019
16008        1      TRIBECA  ...    9718000  03/21/2019

[3 rows x 21 columns]

In [109]:
# What are the building class categories?
# How frequently does each occur?
tribeca_single['BUILDING_CLASS_CATEGORY'].value_counts()

13 CONDOS - ELEVATOR APARTMENTS               121
15 CONDOS - 2-10 UNIT RESIDENTIAL               8
16 CONDOS - 2-10 UNIT WITH COMMERCIAL UNIT      1
46 CONDO STORE BUILDINGS                        1
Name: BUILDING_CLASS_CATEGORY, dtype: int64

In [111]:
# Keep subset of rows:
# Sale price more than $0, 
# Building class category = Condos - Elevator Apartments

# Check how many rows you have now. (Should be 106 rows.)
elevator = tribeca_single['BUILDING_CLASS_CATEGORY']=='13 CONDOS - ELEVATOR APARTMENTS'
non_zero = tribeca_single['SALE_PRICE']>0
tribeca_sub = tribeca_single[elevator & non_zero]
tribeca_sub.shape

(106, 21)

In [116]:
# Make a Plotly Express scatter plot of GROSS_SQUARE_FEET vs SALE_PRICE
import plotly.express as px
lp = px.scatter(tribeca_sub, x='GROSS_SQUARE_FEET', y='SALE_PRICE')
lp.show()

In [117]:
# Add an OLS (Ordinary Least Squares) trendline,
# to see how the outliers influence the "line of best fit"
lp = px.scatter(tribeca_sub, x='GROSS_SQUARE_FEET', y='SALE_PRICE', trendline='ols')
lp.show()

/usr/local/lib/python3.6/dist-packages/statsmodels/tools/_testing.py:19: FutureWarning:

pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.



In [118]:
# Look at sales for more than $35 million

# All are at 70 Vestry Street
# All but one have the same SALE_PRICE & SALE_DATE
# Was the SALE_PRICE for each? Or in total?
# Is this dirty data?
tribeca_sub[tribeca_sub['SALE_PRICE']>35000000]

BOROUGH NEIGHBORHOOD  ... SALE_PRICE   SALE_DATE
8370        1      TRIBECA  ...   36681561  02/12/2019
8371        1      TRIBECA  ...   36681561  02/12/2019
8372        1      TRIBECA  ...   36681561  02/12/2019
8373        1      TRIBECA  ...   36681561  02/12/2019
8374        1      TRIBECA  ...   36681561  02/12/2019
8375        1      TRIBECA  ...   36681561  02/12/2019
8376        1      TRIBECA  ...   36681561  02/12/2019
8377        1      TRIBECA  ...   36681561  02/12/2019
8378        1      TRIBECA  ...   36681561  02/12/2019
8379        1      TRIBECA  ...   36681561  02/12/2019
8380        1      TRIBECA  ...   36681561  02/12/2019
8381        1      TRIBECA  ...   36681561  02/12/2019
8382        1      TRIBECA  ...   36681561  02/12/2019
8383        1      TRIBECA  ...   36681561  02/12/2019
8384        1      TRIBECA  ...   36681561  02/12/2019
9236        1      TRIBECA  ...   39285000  02/15/2019

[16 rows x 21 columns]

In [119]:
# Make a judgment call:
# Keep rows where sale price was < $35 million

# Check how many rows you have now. (Should be down to 90 rows.)
tribeca_clean = tribeca_sub[tribeca_sub['SALE_PRICE']<35000000]
tribeca_clean.shape

(90, 21)

In [120]:
# Now that you've removed outliers,
# Look again at a scatter plot with OLS (Ordinary Least Squares) trendline
lp = px.scatter(tribeca_clean, x='GROSS_SQUARE_FEET', y='SALE_PRICE', trendline='ols')
lp.show()

In [124]:
# Select these columns, then write to a csv file named tribeca.csv. Don't include the index.
tribeca_export = tribeca_clean[['SALE_PRICE', 'GROSS_SQUARE_FEET']]
tribeca_export.to_csv('tribeca.csv', index=False)